In [1]:
import warnings
warnings.filterwarnings('ignore')

import os
import pandas as pd
import numpy as np
from sqlalchemy import create_engine, Column, Integer, String, Float
from sqlalchemy.ext.declarative import declarative_base
Base = declarative_base()

from sqlalchemy.orm import Session
import datetime as dt

In [2]:
violation_file = os.path.join('Speed_Camera_Violations.csv')
station_file = os.path.join('Stations', 'Divvy_Stations_2017_Q3Q4.csv')

In [3]:
# Read witih Pandas
violations_df = pd.read_csv(violation_file)
stations_df = pd.read_csv(station_file)

In [4]:
stations_df.head()
# violations_df.head()

id                    name     city   latitude  longitude  dpcapacity  \
0   2     Buckingham Fountain  Chicago  41.876393 -87.620328          27   
1   3          Shedd Aquarium  Chicago  41.867226 -87.615355          55   
2   4          Burnham Harbor  Chicago  41.856268 -87.613348          23   
3   5  State St & Harrison St  Chicago  41.874053 -87.627716          23   
4   6          Dusable Harbor  Chicago  41.885041 -87.612794          39   

       online_date  Unnamed: 7  
0  6/10/2013 10:43         NaN  
1  6/10/2013 10:44         NaN  
2  6/10/2013 10:46         NaN  
3  6/10/2013 10:46         NaN  
4  6/10/2013 11:18         NaN

In [5]:
del stations_df['Unnamed: 7']   


In [6]:

stations_df['online_date'] = pd.to_datetime(stations_df['online_date'])
stations_df['online_date'] = stations_df['online_date'].dt.date
stations_df.rename(index=str, columns={"id": "station_id", "name":"station_name", "dpcapacity":"capacity"},inplace=True)
stations_df.head()


station_id            station_name     city   latitude  longitude  \
0           2     Buckingham Fountain  Chicago  41.876393 -87.620328   
1           3          Shedd Aquarium  Chicago  41.867226 -87.615355   
2           4          Burnham Harbor  Chicago  41.856268 -87.613348   
3           5  State St & Harrison St  Chicago  41.874053 -87.627716   
4           6          Dusable Harbor  Chicago  41.885041 -87.612794   

   capacity online_date  
0        27  2013-06-10  
1        55  2013-06-10  
2        23  2013-06-10  
3        23  2013-06-10  
4        39  2013-06-10

In [7]:
violations_df['violation_id'] = violations_df.index
violations_df['VIOLATION DATE'] = pd.to_datetime(violations_df['VIOLATION DATE'])
violations_df['VIOLATION DATE'] = violations_df['VIOLATION DATE'].dt.date
violations_df.rename(index=str, columns={"CAMERA ID": "camera_id", "VIOLATION DATE":"violation_date", "X COORDINATE":"x_coordinate", "Y COORDINATE":"y_coordinate"},inplace=True)


In [8]:
violations_df.head()

ADDRESS camera_id violation_date  VIOLATIONS  x_coordinate  \
0       6514 W BELMONT AVE    CHI106     2014-07-01        10.0   1132317.345   
1       6443 W BELMONT AVE    CHI105     2014-07-01         3.0   1132715.909   
2  3116 N NARRAGANSETT AVE    CHI132     2014-07-01        20.0   1133159.075   
3  3115 N NARRAGANSETT AVE    CHI104     2014-07-01        10.0   1133239.690   
4    6226 W IRVING PARK RD    CHI083     2014-07-01        91.0   1133995.170   

   y_coordinate   LATITUDE  LONGITUDE  \
0   1920604.475  41.938377 -87.789119   
1   1920535.619  41.938181 -87.787655   
2   1920109.559  41.937004 -87.786037   
3   1920090.575  41.936951 -87.785741   
4   1925971.269  41.953075 -87.782826   

                                   LOCATION  violation_id  
0   (41.93837715933998, -87.78911871294291)             0  
1  (41.938181258548575, -87.78765548502582)             1  
2   (41.93700435024341, -87.78603672187927)             2  
3   (41.93695084197675, -87.78574089058974)             3  
4   (41.95307482555687, -87.78282553773761)             4

In [9]:
# Define a Base class for Station
class Stations(Base):
    __tablename__ = "stations"
    
    station_id = Column(Integer, primary_key=True)
    station_name = Column(String)
    city = Column(String)
    latitude = Column(Float)
    longitude = Column(Float)
    capacity = Column(Integer)
    online_date = Column(String)


In [10]:
# Define a Base class for Violations
class Violations(Base):
    __tablename__ = "violations"
    
    address = Column(String)
    camera_id = Column(String)
    violation_date = Column(String)
    violations = Column(Float)
    x_coordinate = Column(Float)
    y_coordinate = Column(Float)
    latitude = Column(Float)
    longitude = Column(Float)
    location = Column(String)
    violation_id = Column(Integer, primary_key=True)



In [11]:
# Create database engine
engine = create_engine("sqlite:///bikeshare_traffic.sqlite")

# Create tables in the database
Base.metadata.create_all(engine)

session = Session(bind=engine)

# Write data stored in a DataFrame to a SQL database
violations_df.to_sql(name='violations', con=engine, if_exists = 'append', index=False)
stations_df.to_sql(name='stations', con=engine, if_exists = 'append', index=False)
session.commit()

In [ ]:
# Query the Stations table
station_list = session.query(Stations)
for station in station_list:
    print(station.station_id, station.station_name, station.city, station.latitude, station.longitude, station.capacity, station.online_date)

2 Buckingham Fountain Chicago 41.876393 -87.620328 27 2013-06-10
3 Shedd Aquarium Chicago 41.86722596 -87.61535539 55 2013-06-10
4 Burnham Harbor Chicago 41.856268 -87.613348 23 2013-06-10
5 State St & Harrison St Chicago 41.874053 -87.627716 23 2013-06-10
6 Dusable Harbor Chicago 41.885040999999994 -87.612794 39 2013-06-10
7 Field Blvd & South Water St Chicago 41.88634906 -87.61751655 19 2013-06-19
9 Leavitt St & Archer Ave Chicago 41.82879202 -87.68060446 19 2013-06-21
11 Jeffery Blvd & 71st St Chicago 41.76663824 -87.57645011 11 2013-06-21
12 South Shore Dr & 71st St Chicago 41.76640946 -87.56568757 15 2013-06-21
13 Wilton Ave & Diversey Pkwy Chicago 41.932418 -87.65270500000001 27 2013-06-22
14 Morgan St & 18th St Chicago 41.858086 -87.651073 15 2013-06-22
15 Racine Ave & 18th St Chicago 41.858166 -87.65649499999999 15 2013-06-22
16 Paulina Ave & North Ave Chicago 41.910337 -87.67007199999999 15 2013-06-22
17 Honore St & Division St Chicago 41.903119000000004 -87.673935 23 2013-06-

334 Lake Shore Dr & Belmont Ave Chicago 41.940775 -87.63919200000001 19 2013-09-26
335 Calumet Ave & 35th St Chicago 41.831379 -87.618034 15 2013-09-26
336 Cottage Grove Ave & 47th St Chicago 41.809855 -87.606755 15 2013-09-26
337 Clark St & Chicago Ave Chicago 41.896544 -87.630931 19 2013-09-26
338 Calumet Ave & 18th St Chicago 41.857611 -87.619407 15 2013-09-26
339 Emerald Ave & 31st St Chicago 41.838198 -87.645143 11 2013-09-27
340 Clark St & Wrightwood Ave Chicago 41.929546 -87.643118 15 2013-10-01
341 Adler Planetarium Chicago 41.866095 -87.60726700000001 39 2013-10-03
342 Wolcott Ave & Polk St Chicago 41.871262 -87.673688 15 2013-10-03
343 Racine Ave & Wrightwood Ave Chicago 41.928886999999996 -87.658971 15 2013-10-03
344 Ravenswood Ave & Lawrence Ave Chicago 41.96909 -87.674237 39 2013-10-03
345 Lake Park Ave & 56th St Chicago 41.793242 -87.58778199999999 19 2013-10-04
346 Ada St & Washington Blvd Chicago 41.88283 -87.661206 15 2013-10-04
347 Ashland Ave & Grace St Chicago 41.95

558 Ashland Ave & Garfield Blvd Chicago 41.792821999999994 -87.664429 11 2016-05-27
559 Racine Ave & Garfield Blvd Chicago 41.794228000000004 -87.655073 11 2016-05-27
560 Marshfield Ave & 59th St Chicago 41.786833 -87.66621500000001 11 2016-05-27
561 Damen Ave & 59th St Chicago 41.78602 -87.67416700000001 11 2016-05-27
562 Racine Ave & 61st St Chicago 41.783189 -87.654372 11 2016-05-27
563 Ashland Ave & 63rd St Chicago 41.779374 -87.664843 15 2016-05-27
564 Racine Ave & 65th St Chicago 41.775393 -87.654308 11 2016-05-27
565 Ashland Ave & 66th St Chicago 41.774074 -87.663815 11 2016-05-27
566 Ashland Ave & 69th St Chicago 41.768726 -87.664069 11 2016-05-27
567 May St & 69th St Chicago 41.768938 -87.652934 11 2016-05-27
568 Normal Ave & 72nd St Chicago 41.763462 -87.637297 11 2016-05-27
569 Woodlawn Ave & 75th St Chicago 41.759159999999994 -87.595751 15 2016-05-27
570 Evans Ave & 75th St Chicago 41.758308 -87.606685 11 2016-05-27
571 Vernon Ave & 75th St Chicago 41.758361 -87.614138 11 2

In [ ]:
# Query the Stations table
violation_list = session.query(Violations)
for violation in violation_list:
    print(violation.address , violation.camera_id ,violation.violation_date ,violation.violations,
          violation.x_coordinate ,violation.y_coordinate ,violation.latitude ,violation.longitude,
          violation.location ,violation.violation_id )
    
   

6514 W BELMONT AVE CHI106 2014-07-01 10.0 1132317.345 1920604.475 41.93837716 -87.78911871 (41.93837715933998, -87.78911871294291) 0
6443 W BELMONT AVE CHI105 2014-07-01 3.0 1132715.909 1920535.619 41.93818126 -87.78765549 (41.938181258548575, -87.78765548502582) 1
3116 N NARRAGANSETT AVE CHI132 2014-07-01 20.0 1133159.075 1920109.5590000001 41.93700435 -87.78603672 (41.93700435024341, -87.78603672187927) 2
3115 N NARRAGANSETT AVE CHI104 2014-07-01 10.0 1133239.69 1920090.575 41.93695084 -87.78574089 (41.93695084197675, -87.78574089058974) 3
6226 W IRVING PARK RD CHI083 2014-07-01 91.0 1133995.17 1925971.269 41.95307483 -87.78282554 (41.95307482555687, -87.78282553773761) 4
6250 W FULLERTON CHI040 2014-07-01 21.0 1134113.482 1915315.344 41.9238317 -87.78264224 (41.92383169923362, -87.78264224184598) 5
6247 W FULLERTON CHI039 2014-07-01 21.0 1134158.2820000001 1915236.511 41.92361458 -87.78247949 (41.9236145831186, -87.78247948955652) 6
5816 W JACKSON CHI058 2014-07-01 91.0 1137564.895 

4446 N BROADWAY CHI097 2014-07-01 1.0 1168458.604 1929791.619 41.96288064 -87.65602445 (41.96288063517309, -87.6560244499908) 73
5420 S RACINE AVE CHI118 2014-07-01 27.0 1169208.6090000002 1868739.47 41.79533278 -87.65504098 (41.795332774848234, -87.65504097855228) 74
2928 S HALSTED CHI117 2014-07-01 3.0 1171407.143 1885330.618 41.84081263 -87.64649261 (41.84081262592384, -87.64649261049526) 75
346 W 76th ST CHI136 2014-07-01 11.0 1175111.6409999998 1854589.689 41.75637436 -87.63381659 (41.7563743554102, -87.6338165847716) 76
341 W 76th ST CHI137 2014-07-01 11.0 1175175.124 1854511.46 41.75615827 -87.63358626 (41.756158269344546, -87.6335862634599) 77
445 W 127TH CHI045 2014-07-01 220.0 1175468.446 1820629.229 41.66317406 -87.63352045 (41.663174059325534, -87.63352045241697) 78
7518 S VINCENNES CHI063 2014-07-01 124.0 1175649.435 1855003.1919999998 41.75749704 -87.63183333 (41.75749703994495, -87.63183332832696) 79
630 S STATE CHI034 2014-07-01 10.0 1176418.005 1897401.385 41.87382421 

4965 S ARCHER CHI032 2014-07-03 77.0 1150880.68 1871373.744 41.80293879 -87.72218179 (41.802938790166, -87.72218179156356) 207
7826 S PULASKI CHI072 2014-07-03 28.0 1151040.68 1852282.476 41.7505462 -87.72209266 (41.75054619772355, -87.72209265589272) 208
7833 S PULASKI CHI071 2014-07-03 126.0 1151122.447 1852224.144 41.75038453 -87.72179454 (41.75038452958284, -87.72179453872008) 209
3832 W 79TH CHI074 2014-07-03 69.0 1151723.353 1851984.505 41.74971518 -87.71959878 (41.749715176851936, -87.71959877920995) 210
3655 W JACKSON CHI008 2014-07-03 15.0 1151781.485 1898394.967 41.87707083 -87.71816832 (41.87707082846323, -87.71816831641307) 211
3646 W MADISON CHI009 2014-07-03 48.0 1151844.874 1899804.753 41.88093819 -87.71789845 (41.88093818643283, -87.71789844857646) 212
3851 W 79th CHI073 2014-07-03 31.0 1151859.078 1851860.0180000002 41.74937091 -87.71910468 (41.74937090787529, -87.71910467544157) 213
3843 W 111TH CHI048 2014-07-03 70.0 1152527.403 1830667.7780000002 41.691202399999995 

2721 W MONTROSE CHI078 2014-07-05 8.0 1157328.845 1929075.39 41.96114938 -87.69696403 (41.96114938287925, -87.69696403378589) 355
2712 W IRVING PARK CHI080 2014-07-05 101.0 1157447.914 1926504.6369999999 41.95409266 -87.6965965 (41.954092657149786, -87.6965965016668) 356
2705 W IRVING PARK CHI079 2014-07-05 96.0 1157555.243 1926426.211 41.95387527 -87.69620409 (41.95387526461699, -87.69620408862693) 357
6523 N WESTERN CHI051 2014-07-05 84.0 1159169.452 1943341.865 42.00025951 -87.68980291 (42.00025951144952, -87.68980290863908) 358
4436 N WESTERN CHI094 2014-07-05 41.0 1159528.873 1929555.551 41.96242185 -87.68886228 (41.9624218495406, -87.68886227502836) 359
4433 N WESTERN CHI055 2014-07-05 43.0 1159610.142 1929516.782 41.96231379 -87.68856455 (41.96231378868856, -87.68856455418805) 360
2513 W 55TH CHI070 2014-07-05 33.0 1160431.749 1868077.675 41.79370225 -87.68724427 (41.79370224937009, -87.68724427195639) 361
4432 N LINCOLN CHI056 2014-07-05 1.0 1160697.51 1929507.414 41.96226556 -

4446 N BROADWAY CHI097 2014-07-06 3.0 1168458.604 1929791.619 41.96288064 -87.65602445 (41.96288063517309, -87.6560244499908) 434
5420 S RACINE AVE CHI118 2014-07-06 28.0 1169208.6090000002 1868739.47 41.79533278 -87.65504098 (41.795332774848234, -87.65504097855228) 435
2928 S HALSTED CHI117 2014-07-06 6.0 1171407.143 1885330.618 41.84081263 -87.64649261 (41.84081262592384, -87.64649261049526) 436
445 W 127TH CHI045 2014-07-06 231.0 1175468.446 1820629.229 41.66317406 -87.63352045 (41.663174059325534, -87.63352045241697) 437
450 N COLUMBUS DR CHI125 2014-07-06 39.0 1178351.216 1903356.802 41.89012235 -87.62046140000001 (41.890122352505166, -87.62046139513696) 438
449 N COLUMBUS DR CHI124 2014-07-06 16.0 1178428.354 1903326.6130000001 41.89003776 -87.62017903 (41.89003775504898, -87.62017903427099) 439
62 E 95TH CHI036 2014-07-06 11.0 1178615.9540000001 1842047.622 41.721878499999995 -87.62135433 (41.72187849819265, -87.62135432849777) 440
536 E MORGAN DR CHI029 2014-07-06 210.0 1180984

...

8345 S ASHLAND AVE CHI168 2016-03-22 33.0 1167170.494 1849194.1169999999 41.74174165 -87.66307333 (41.741741651401504, -87.66307332925098) 61882
1507 W 83rd ST CHI170 2016-03-22 3.0 1167695.17 1849654.229 41.74299304 -87.66113776 (41.742993034938884, -87.66113775973551) 61883
1142 W IRVING PARK CHI095 2016-03-22 59.0 1167789.529 1926747.1069999998 41.95454087 -87.65857252 (41.95454086624301, -87.65857252142276) 61884
1334 W GARFIELD BLVD CHI119 2016-03-22 97.0 1168211.289 1868328.466 41.79422647 -87.65871 (41.79422646635146, -87.65870999891658) 61885
1315 W GARFIELD BLVD CHI121 2016-03-22 48.0 1168444.53 1868118.435 41.79364509 -87.65786076 (41.793645091444645, -87.6578607639445) 61886
4446 N BROADWAY CHI097 2016-03-22 3.0 1168458.604 1929791.619 41.96288064 -87.65602445 (41.96288063517309, -87.6560244499908) 61887
4429 N BROADWAY CHI096 2016-03-22 3.0 1168597.252 1929689.186 41.96259655 -87.65551768 (41.962596548691735, -87.65551767517252) 61888
5420 S RACINE AVE CHI118 2016-03-22 8.0

319 E ILLINOIS ST CHI126 2016-03-23 2.0 1178652.116 1903646.3769999999 41.8909101 -87.61934752 (41.89091009572781, -87.61934752145963) 62034
215 E 63RD ST CHI146 2016-03-23 71.0 1178876.8159999999 1863250.968 41.78005699 -87.61975472 (41.78005698693417, -87.6197547203603) 62035
6330 S MARTIN LUTHER KING CHI148 2016-03-23 21.0 1179971.443 1862983.346 41.77929761 -87.61574988 (41.77929760923632, -87.61574987538572) 62036
536 E MORGAN DR CHI029 2016-03-23 69.0 1180984.6570000001 1868164.7659999998 41.79349265 -87.61187597 (41.793492645896656, -87.6118759701359) 62037
5330 S COTTAGE GROVE CHI013 2016-03-23 32.0 1182452.725 1869711.794 41.79770389 -87.60644478 (41.79770388561477, -87.60644477865196) 62038
1901 E 75TH ST CHI138 2016-03-23 6.0 1190192.11 1855579.523 41.75874077 -87.57851859 (41.758740770124234, -87.57851859043261) 62039
7422 S JEFFERY CHI101 2016-03-23 13.0 1190789.832 1856045.67 41.76000551 -87.57631298 (41.760005504685466, -87.57631298283938) 62040
2109 E 87TH ST CHI145 201

4620 W BELMONT AVE CHI086 2016-03-25 6.0 1144830.584 1920910.013 41.93898839 -87.74312142 (41.938988390759555, -87.74312142256439) 62181
4124 W FOSTER AVE CHI003 2016-03-25 139.0 1147852.5890000002 1934274.995 41.9756053 -87.73166979999999 (41.97560530194193, -87.73166979484374) 62182
5120 N PULASKI CHI004 2016-03-25 49.0 1148759.386 1933817.6 41.97433266 -87.72834702 (41.97433265461055, -87.72834702238127) 62183
4053 W NORTH AVE CHI159 2016-03-25 12.0 1148866.624 1910281.5380000002 41.90974567 -87.72856329999999 (41.90974567444195, -87.72856329512945) 62184
4042 W NORTH AVE CHI161 2016-03-25 22.0 1149005.647 1910365.1509999998 41.90997243 -87.72805041 (41.90997242450237, -87.72805040969816) 62185
1754 N PULASKI RD CHI157 2016-03-25 8.0 1149394.777 1911607.8 41.91337483 -87.7265886 (41.91337483050126, -87.72658859994081) 62186
3655 W JACKSON CHI008 2016-03-25 31.0 1151781.485 1898394.967 41.87707083 -87.71816832 (41.87707082846323, -87.71816831641307) 62187
3646 W MADISON CHI009 2016-0

3100 W AUGUSTA CHI011 2016-03-27 22.0 1155438.363 1906531.351 41.89932514 -87.70452235 (41.89932514072566, -87.70452234551168) 62333
3047 W JACKSON BLVD CHI122 2016-03-27 11.0 1155924.804 1898487.6909999999 41.87724277 -87.70295269 (41.877242773826396, -87.7029526885659) 62334
6818 S KEDZIE CHI018 2016-03-27 28.0 1156183.476 1859144.994 41.76927622 -87.7030626 (41.769276221338444, -87.70306259506) 62335
6909 S KEDZIE CHI014 2016-03-27 51.0 1156276.175 1858582.894 41.76773187 -87.70273791 (41.76773186901884, -87.70273790708362) 62336
2917 W ROOSEVELT CHI019 2016-03-27 42.0 1156991.618 1894531.138 41.86636402 -87.69914297 (41.866364024167034, -87.69914296647906) 62337
2912 W ROOSEVELT CHI020 2016-03-27 21.0 1157040.213 1894612.128 41.86658528 -87.69896238 (41.86658528313424, -87.69896237494204) 62338
2900 W OGDEN CHI021 2016-03-27 156.0 1157135.92 1892361.676 41.86040786 -87.6986721 (41.86040786445197, -87.69867209877323) 62339
2721 W MONTROSE CHI078 2016-03-27 4.0 1157328.845 1929075.39

8318 S ASHLAND AVE CHI169 2016-03-28 40.0 1167083.227 1849460.261 41.74247386 -87.66338548 (41.74247385456547, -87.66338547998558) 62483
1507 W 83rd ST CHI170 2016-03-28 14.0 1167695.17 1849654.229 41.74299304 -87.66113776 (41.742993034938884, -87.66113775973551) 62484
1142 W IRVING PARK CHI095 2016-03-28 87.0 1167789.529 1926747.1069999998 41.95454087 -87.65857252 (41.95454086624301, -87.65857252142276) 62485
1334 W GARFIELD BLVD CHI119 2016-03-28 122.0 1168211.289 1868328.466 41.79422647 -87.65871 (41.79422646635146, -87.65870999891658) 62486
1315 W GARFIELD BLVD CHI121 2016-03-28 44.0 1168444.53 1868118.435 41.79364509 -87.65786076 (41.793645091444645, -87.6578607639445) 62487
4446 N BROADWAY CHI097 2016-03-28 3.0 1168458.604 1929791.619 41.96288064 -87.65602445 (41.96288063517309, -87.6560244499908) 62488
5420 S RACINE AVE CHI118 2016-03-28 13.0 1169208.6090000002 1868739.47 41.79533278 -87.65504098 (41.795332774848234, -87.65504097855228) 62489
2928 S HALSTED CHI117 2016-03-28 7.0